# Intro to Recommender Systems Lab

Complete the exercises below to solidify your knowledge and understanding of recommender systems.

For this lab, we are going to be putting together a user similarity based recommender system in a step-by-step fashion. Our data set contains customer grocery purchases, and we will use similar purchase behavior to inform our recommender system. Our recommender system will generate 5 recommendations for each customer based on the purchases they have made.

In [76]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
#import cufflinks as cf
#cf.go_offline()

# Scipy
from scipy.spatial.distance import pdist, squareform   # conda install -c anaconda scipy

In [77]:
data = pd.read_csv('../data/customer_product_sales.csv')

In [78]:
data.head()

CustomerID FirstName   LastName  SalesID  ProductID           ProductName  \
0       61288      Rosa   Andersen   134196        229  Bread - Hot Dog Buns   
1       77352     Myron     Murray  6167892        229  Bread - Hot Dog Buns   
2       40094     Susan  Stevenson  5970885        229  Bread - Hot Dog Buns   
3       23548    Tricia    Vincent  6426954        229  Bread - Hot Dog Buns   
4       78981     Scott      Burch   819094        229  Bread - Hot Dog Buns   

   Quantity  
0        16  
1        20  
2        11  
3         6  
4        20

## Step 1: Create a data frame that contains the total quantity of each product purchased by each customer.

You will need to group by CustomerID and ProductName and then sum the Quantity field.

In [79]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 68584 entries, 0 to 68583
Data columns (total 7 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   CustomerID   68584 non-null  int64 
 1   FirstName    68584 non-null  object
 2   LastName     68584 non-null  object
 3   SalesID      68584 non-null  int64 
 4   ProductID    68584 non-null  int64 
 5   ProductName  68584 non-null  object
 6   Quantity     68584 non-null  int64 
dtypes: int64(4), object(3)
memory usage: 3.7+ MB


In [87]:
data.groupby(["CustomerID","ProductName"])['Quantity'].sum().reset_index()


CustomerID                    ProductName  Quantity
0              33               Apricots - Dried         1
1              33              Assorted Desserts         1
2              33        Bandage - Flexible Neon         1
3              33  Bar Mix - Pina Colada, 355 Ml         1
4              33         Beans - Kidney, Canned         1
...           ...                            ...       ...
63623       98200                   Vol Au Vents        50
63624       98200                  Wasabi Powder        25
63625       98200       Wine - Fume Blanc Fetzer        25
63626       98200  Wine - Hardys Bankside Shiraz        25
63627       98200        Yogurt - French Vanilla        25

[63628 rows x 3 columns]

## Step 2: Use the `pivot_table` method to create a product by customer matrix.

The rows of the matrix should represent the products, the columns should represent the customers, and the values should be the quantities of each product purchased by each customer. You will also need to replace nulls with zeros, which you can do using the `fillna` method.

In [8]:
data.fillna(0)

CustomerID FirstName   LastName  SalesID  ProductID  \
0           61288      Rosa   Andersen   134196        229   
1           77352     Myron     Murray  6167892        229   
2           40094     Susan  Stevenson  5970885        229   
3           23548    Tricia    Vincent  6426954        229   
4           78981     Scott      Burch   819094        229   
...           ...       ...        ...      ...        ...   
68579       94547    Gerald    Donovan   687884        211   
68580       57654  Lashonda        Roy  4373415        211   
68581       36751      Glen  Frederick  2405597        211   
68582       43270     Devon  Mc Daniel  4328852        211   
68583       78718     Mandy     Abbott  6175098        211   

                         ProductName  Quantity  
0               Bread - Hot Dog Buns        16  
1               Bread - Hot Dog Buns        20  
2               Bread - Hot Dog Buns        11  
3               Bread - Hot Dog Buns         6  
4               Bread - Hot Dog Buns        20  
...                              ...       ...  
68579  Wine - Prosecco Valdobiaddene        24  
68580  Wine - Prosecco Valdobiaddene        15  
68581  Wine - Prosecco Valdobiaddene        10  
68582  Wine - Prosecco Valdobiaddene        11  
68583  Wine - Prosecco Valdobiaddene        20  

[68584 rows x 7 columns]

In [9]:
data.describe()

CustomerID       SalesID     ProductID      Quantity
count  68584.000000  6.858400e+04  68584.000000  68584.000000
mean   49093.982051  3.375808e+06    226.328779     12.911160
std    28856.408623  1.954588e+06    130.635144      7.301238
min       33.000000  1.620000e+02      1.000000      1.000000
25%    23220.000000  1.687831e+06    113.000000      6.000000
50%    49795.000000  3.371146e+06    226.000000     13.000000
75%    75793.000000  5.058868e+06    340.000000     20.000000
max    98200.000000  6.758117e+06    452.000000     25.000000

In [10]:
pivot_data = pd.pivot_table(data, values='Quantity', index=['ProductName'], columns=['CustomerID'], aggfunc=np.mean)
pivot_data_na = pivot_data.fillna(0)
pivot_data_T=pivot_data_na.T
pivot_data_T


ProductName  Anchovy Paste - 56 G Tube  Appetizer - Mini Egg Roll, Shrimp  \
CustomerID                                                                  
33                                 0.0                                0.0   
200                                0.0                                0.0   
264                                0.0                                0.0   
356                                0.0                                0.0   
412                                0.0                                0.0   
...                                ...                                ...   
97928                              0.0                                0.0   
98069                              0.0                                0.0   
98159                              0.0                                0.0   
98185                              0.0                                0.0   
98200                              0.0                                0.0   

ProductName  Appetizer - Mushroom Tart  Appetizer - Sausage Rolls  \
CustomerID                                                          
33                                 0.0                        0.0   
200                                0.0                        0.0   
264                                0.0                        0.0   
356                                0.0                        0.0   
412                                0.0                        0.0   
...                                ...                        ...   
97928                              0.0                       25.0   
98069                              0.0                       25.0   
98159                              0.0                        0.0   
98185                             25.0                       25.0   
98200                              0.0                        0.0   

ProductName  Apricots - Dried  Apricots - Halves  Apricots Fresh  \
CustomerID                                                         
33                        1.0                0.0             0.0   
200                       0.0                0.0             0.0   
264                       0.0                1.0             1.0   
356                       0.0                0.0             0.0   
412                       1.0                0.0             0.0   
...                       ...                ...             ...   
97928                     0.0               25.0             0.0   
98069                     0.0               25.0             0.0   
98159                     0.0                0.0             0.0   
98185                     0.0               25.0             0.0   
98200                     0.0               25.0            25.0   

ProductName  Arizona - Green Tea  Artichokes - Jerusalem  Assorted Desserts  \
CustomerID                                                                    
33                           0.0                     0.0                1.0   
200                          0.0                     0.0                0.0   
264                          0.0                     0.0                0.0   
356                          0.0                     0.0                0.0   
412                          0.0                     0.0                0.0   
...                          ...                     ...                ...   
97928                       25.0                     0.0                0.0   
98069                        0.0                     0.0               25.0   
98159                        0.0                     0.0                0.0   
98185                        0.0                     0.0                0.0   
98200                        0.0                     0.0               25.0   

ProductName  ...  Wine - White, Colubia Cresh  Wine - White, Mosel Gold  \
CustomerID   ...                                                          
33           ...                     

## Step 3: Create a customer similarity matrix using `squareform` and `pdist`. For the distance metric, choose "euclidean."

In [548]:
pivot_data_T.head()

ProductName  Anchovy Paste - 56 G Tube  Appetizer - Mini Egg Roll, Shrimp  \
CustomerID                                                                  
33                                 0.0                                0.0   
200                                0.0                                0.0   
264                                0.0                                0.0   
356                                0.0                                0.0   
412                                0.0                                0.0   

ProductName  Appetizer - Mushroom Tart  Appetizer - Sausage Rolls  \
CustomerID                                                          
33                                 0.0                        0.0   
200                                0.0                        0.0   
264                                0.0                        0.0   
356                                0.0                        0.0   
412                                0.0                        0.0   

ProductName  Apricots - Dried  Apricots - Halves  Apricots Fresh  \
CustomerID                                                         
33                        1.0                0.0             0.0   
200                       0.0                0.0             0.0   
264                       0.0                1.0             1.0   
356                       0.0                0.0             0.0   
412                       1.0                0.0             0.0   

ProductName  Arizona - Green Tea  Artichokes - Jerusalem  Assorted Desserts  \
CustomerID                                                                    
33                           0.0                     0.0                1.0   
200                          0.0                     0.0                0.0   
264                          0.0                     0.0                0.0   
356                          0.0                     0.0                0.0   
412                          0.0                     0.0                0.0   

ProductName  ...  Wine - White, Colubia Cresh  Wine - White, Mosel Gold  \
CustomerID   ...                                                          
33           ...                          0.0                       0.0   
200          ...                          1.0                       0.0   
264          ...                          0.0                       0.0   
356          ...                          0.0                       0.0   
412          ...                          0.0                       1.0   

ProductName  Wine - White, Schroder And Schyl  Wine - Wyndham Estate Bin 777  \
CustomerID                                                                     
33                                        0.0                            0.0   
200                                       0.0                            0.0   
264                                       0.0                            1.0   
356                                       0.0                            0.0   
412                                       1.0                            1.0   

ProductName  Wonton Wrappers  Yeast Dry - Fermipan  Yoghurt Tubes  \
CustomerID                                                          
33                       0.0                   0.0            0.0   
200                      0.0                   0.0            0.0   
264                      0.0                   0.0            0.0   
356                      0.0                   0.0            0.0   
412                      0.0                   0.0            0.0   

ProductName  Yogurt - Blueberry, 175 Gr  Yogurt - French Vanilla  \
CustomerID                                                         
33                                  0.0                      1.0   
200                                 1.0                      0.0   
264                                 0.0                      0.0   
356                               

In [549]:
dist_calculation = pdist(X=pivot_data_T, metric='euclidean')
dist_calculation


array([ 10.72380529,   9.64365076,   9.89949494, ..., 266.9269563 ,
       266.9269563 , 269.25824036])

In [550]:
dist_distribution = squareform(dist_calculation)
dist_distribution

array([[  0.        ,  10.72380529,   9.64365076, ..., 197.94948851,
        218.8241303 , 203.79892051],
       [ 10.72380529,   0.        ,  10.67707825, ..., 197.34994299,
        218.62525014, 203.95342606],
       [  9.64365076,  10.67707825,   0.        , ..., 197.32460566,
        218.02981447, 203.80628057],
       ...,
       [197.94948851, 197.34994299, 197.32460566, ...,   0.        ,
        266.9269563 , 266.9269563 ],
       [218.8241303 , 218.62525014, 218.02981447, ..., 266.9269563 ,
          0.        , 269.25824036],
       [203.79892051, 203.95342606, 203.80628057, ..., 266.9269563 ,
        269.25824036,   0.        ]])

In [551]:
euclid_dist = pd.DataFrame(dist_distribution,
                           index=pivot_data_T.index,
                           columns=pivot_data_T.index)

euclid_dist

CustomerID       33          200         264         356         412    \
CustomerID                                                               
33            0.000000   10.723805    9.643651    9.899495   10.440307   
200          10.723805    0.000000   10.677078   10.723805   11.489125   
264           9.643651   10.677078    0.000000   10.344080   10.198039   
356           9.899495   10.723805   10.344080    0.000000   10.630146   
412          10.440307   11.489125   10.198039   10.630146    0.000000   
...                ...         ...         ...         ...         ...   
97928       198.075743  197.729613  196.817174  197.575302  197.339808   
98069       203.921554  202.723950  203.315026  204.293906  204.066166   
98159       197.949489  197.349943  197.324606  197.322072  197.466453   
98185       218.824130  218.625250  218.029814  218.142155  217.928887   
98200       203.798921  203.953426  203.806281  203.681123  202.960587   

CustomerID       464         477         639         649         669    ...  \
CustomerID                                                              ...   
33           10.148892   10.723805   10.246951   10.344080   10.148892  ...   
200          11.045361   10.770330   10.954451   10.677078   10.488088  ...   
264          10.488088   10.677078   10.583005   10.488088   10.488088  ...   
356          10.535654   10.630146    9.949874   10.630146   10.440307  ...   
412          10.677078   10.677078   10.198039   10.770330   10.392305  ...   
...                ...         ...         ...         ...         ...  ...   
97928       197.324606  197.339808  197.441130  197.451260  197.699267  ...   
98069       204.051464  203.821000  203.919102  203.683578  203.678668  ...   
98159       197.451260  197.466453  197.694208  197.197870  197.572771  ...   
98185       218.487986  218.501716  218.135279  218.373533  218.940631  ...   
98200       203.192027  203.698306  203.796467  204.051464  203.310108  ...   

CustomerID       97697       97753       97769       97793       97900  \
CustomerID                                                               
33          206.963765  194.766527  199.145675  183.463893  202.259734   
200         206.269242  194.285872  198.423789  182.543146  202.044550   
264         206.366179  194.517351  199.153207  182.789496  201.772149   
356         206.726873  194.643263  199.025124  182.923481  202.264678   
412         206.985507  193.889144  199.168271  182.805908  202.034650   
...                ...         ...         ...         ...         ...   
97928       266.926956  252.487623  265.753645  246.221445  251.246891   
98069       273.861279  264.575131  268.095132  263.391344  256.173769   
98159       266.926956  250.000000  258.602011  256.173769  261.007663   
98185       287.228132  287.228132  272.717803  265.753645  279.508497   
98200       273.861279  266.926956  261.007663  261.007663  263.391344   

CustomerID       97928       98069       98159       98185       98200  
CustomerID                                                              
33          198.075743  203.921554  197.949489  218.824130  203.798921  
200         197.729613  202.723950  197.349943  218.625250  203.953426  
264         196.817174  203.315026  197.324606  218.029814  203.806281  
356         197.575302  204.293906  197.322072  218.142155  203.681123  
412         197.339808  204.066166  197.466453  217.928887  202.960587  
...                ...         ...         ...         ...         ...  
97928         0.000000  252.487623  252.487623  278.388218  276.134025  
98069       252.487623    0.000000  254.950976  276.134025  264.575131  
98159       252.487623  254.950976    0.000000  266.926956  266.926956  
98185       278.388218  276.134025  266.926956    0.000000  269.258240  
98200       276.134025  264.575131  266.926956  269.258240    0.000000  

[1000 rows x 1000 columns]

In [15]:
euclid_dist_norm = pd.DataFrame(1/(1 + squareform(pdist(pivot_data_T, 'euclidean'))),
                               index=pivot_data_T.index,
                                columns=pivot_data_T.index)

euclid_dist_norm

CustomerID     33        200       264       356       412       464    \
CustomerID                                                               
33          1.000000  0.085297  0.093953  0.091747  0.087410  0.089695   
200         0.085297  1.000000  0.085638  0.085297  0.080070  0.083020   
264         0.093953  0.085638  1.000000  0.088152  0.089301  0.087047   
356         0.091747  0.085297  0.088152  1.000000  0.085983  0.086688   
412         0.087410  0.080070  0.089301  0.085983  1.000000  0.085638   
...              ...       ...       ...       ...       ...       ...   
97928       0.005023  0.005032  0.005055  0.005036  0.005042  0.005042   
98069       0.004880  0.004909  0.004894  0.004871  0.004876  0.004877   
98159       0.005026  0.005042  0.005042  0.005042  0.005039  0.005039   
98185       0.004549  0.004553  0.004566  0.004563  0.004568  0.004556   
98200       0.004883  0.004879  0.004883  0.004886  0.004903  0.004897   

CustomerID     477       639       649       669    ...     97697     97753  \
CustomerID                                          ...                       
33          0.085297  0.088913  0.088152  0.089695  ...  0.004809  0.005108   
200         0.084959  0.083651  0.085638  0.087047  ...  0.004825  0.005121   
264         0.085638  0.086333  0.087047  0.087047  ...  0.004822  0.005115   
356         0.085983  0.091325  0.085983  0.087410  ...  0.004814  0.005111   
412         0.085638  0.089301  0.084959  0.087779  ...  0.004808  0.005131   
...              ...       ...       ...       ...  ...       ...       ...   
97928       0.005042  0.005039  0.005039  0.005033  ...  0.003732  0.003945   
98069       0.004882  0.004880  0.004886  0.004886  ...  0.003638  0.003765   
98159       0.005039  0.005033  0.005045  0.005036  ...  0.003732  0.003984   
98185       0.004556  0.004563  0.004558  0.004547  ...  0.003469  0.003469   
98200       0.004885  0.004883  0.004877  0.004895  ...  0.003638  0.003732   

CustomerID     97769     97793     97900     97928     98069     98159  \
CustomerID                                                               
33          0.004996  0.005421  0.004920  0.005023  0.004880  0.005026   
200         0.005014  0.005448  0.004925  0.005032  0.004909  0.005042   
264         0.004996  0.005441  0.004932  0.005055  0.004894  0.005042   
356         0.004999  0.005437  0.004920  0.005036  0.004871  0.005042   
412         0.004996  0.005441  0.004925  0.005042  0.004876  0.005039   
...              ...       ...       ...       ...       ...       ...   
97928       0.003749  0.004045  0.003964  1.000000  0.003945  0.003945   
98069       0.003716  0.003782  0.003888  0.003945  1.000000  0.003907   
98159       0.003852  0.003888  0.003817  0.003945  0.003907  1.000000   
98185       0.003653  0.003749  0.003565  0.003579  0.003608  0.003732   
98200       0.003817  0.003817  0.003782  0.003608  0.003765  0.003732   

CustomerID     98185     98200  
CustomerID                      
33          0.004549  0.004883  
200         0.004553  0.004879  
264         0.004566  0.004883  
356         0.004563  0.004886  
412         0.004568  0.004903  
...              ...       ...  
97928       0.003579  0.003608  
98069       0.003608  0.003765  
98159       0.003732  0.003732  
98185       1.000000  0.003700  
98200       0.003700  1.000000  

[1000 rows x 1000 columns]

## Step 4: Check your results by generating a list of the top 5 most similar customers for a specific CustomerID.

In [64]:
euclid_dist_norm.columns

Int64Index([   33,   200,   264,   356,   412,   464,   477,   639,   649,
              669,
            ...
            97697, 97753, 97769, 97793, 97900, 97928, 98069, 98159, 98185,
            98200],
           dtype='int64', name='CustomerID', length=1000)

In [62]:
#top_5 = euclid_dist_norm[18688].sort_values(ascending=False)

def posicion(x):
    for x in euclid_dist_norm[x]:
        top_5 = euclid_dist_norm[x].sort_values(ascending=False)
        return print(top_5.head(6))

In [256]:
posicion([33])

CustomerID
33      1.000000
3909    0.095358
3531    0.093953
264     0.093953
2503    0.093498
3305    0.093051
Name: 33, dtype: float64


In [259]:
top_5 = euclid_dist_norm[33].sort_values(ascending=False)
top_5.head(6)

CustomerID
33      1.000000
3909    0.095358
3531    0.093953
264     0.093953
2503    0.093498
3305    0.093051
Name: 33, dtype: float64

In [260]:
euclid_simil_items = dict(top_5.head(6).items())
euclid_simil_items

{33: 1.0,
 3909: 0.09535767393825997,
 3531: 0.0939527256629669,
 264: 0.0939527256629669,
 2503: 0.0934984915573404,
 3305: 0.09305100366818048}

## Step 5: From the data frame you created in Step 1, select the records for the list of similar CustomerIDs you obtained in Step 4.

In [269]:
df_step5 = data.groupby(["CustomerID","ProductName"])['Quantity'].sum().reset_index()

t5= top_5.head(6) #lo guardamos en una variable mejor 

df_records = df_step5[df_step5["CustomerID"] == list(t5.index)[4]]
#de los top 5/6 CustomerID , miramos la posición del CustomerID 2503 por ejemplo que es la posición 4 
df_records.sort_values("Quantity", ascending=False)


CustomerID                        ProductName  Quantity
1888        2503              Knife Plastic - White         2
1868        2503  Bar - Granola Trail Mix Fruit Nut         2
1875        2503                  Butter - Unsalted         2
1901        2503                    Sausage - Liver         1
1892        2503             Pants Custom Dry Clean         1
1893        2503       Pastry - Cheese Baked Scones         1
1894        2503                 Peas - Pigeon, Dry         1
1895        2503               Pepsi - Diet, 355 Ml         1
1896        2503        Pork - Bacon, Double Smoked         1
1897        2503                Raspberries - Fresh         1
1898        2503                   Salsify, Organic         1
1899        2503                Sauce - Hollandaise         1
1900        2503                Sausage - Breakfast         1
1902        2503         Soup - Campbells, Cream Of         1
1890        2503             Nut - Chestnuts, Whole         1
1903        2503       Soup - Canadian Pea, Dry Mix         1
1904        2503                 Tea - Decaf Lipton         1
1905        2503                          Tia Maria         1
1906        2503                  Veal - Sweetbread         1
1907        2503         Wine - Crozes Hermitage E.         1
1908        2503         Wine - Magnotta - Cab Sauv         1
1909        2503                Wine - Red, Cooking         1
1910        2503   Wine - White, Schroder And Schyl         1
1891        2503   Oil - Shortening - All - Purpose         1
1865        2503          Appetizer - Mushroom Tart         1
1889        2503               Lamb - Pieces, Diced         1
1866        2503          Appetizer - Sausage Rolls         1
1867        2503              Bandage - Fexible 1x3         1
1869        2503     Beef - Montreal Smoked Brisket         1
1870        2503           Beef - Top Sirloin - Aaa         1
1871        2503                 Beef Ground Medium         1
1872        2503        Beets - Candy Cane, Organic         1
1873        2503             Bread - English Muffin         1
1874        2503               Bread Crumbs - Panko         1
1876        2503         Cake - Cake Sheet Macaroon         1
1877        2503   Cheese - Boursin, Garlic / Herbs         1
1878        2503           Cheese - Taleggio D.o.p.         1
1879        2503                      Chef Hat 20cm         1
1880        2503             Coffee Decaf Colombian         1
1881        2503                    Cream Of Tartar         1
1882        2503                    Extract - Lemon         1
1883        2503                     Fond - Neutral         1
1884        2503                      Hersey Shakes         1
1885        2503      Ice Cream Bar - Hageen Daz To         1
1886        2503                       Juice - Lime         1
1887        2503                   Ketchup - Tomato         1
1911        2503                      Yoghurt Tubes         1

## Step 6: Aggregate those customer purchase records by ProductName, sum the Quantity field, and then rank them in descending order by quantity.

This will give you the total number of each product purchased by the 5 most similar customers to the customer you selected in order from most purchased to least.

In [270]:
df_rank = df_records.sort_values("Quantity", ascending=False)
df_rank


CustomerID                        ProductName  Quantity
1888        2503              Knife Plastic - White         2
1868        2503  Bar - Granola Trail Mix Fruit Nut         2
1875        2503                  Butter - Unsalted         2
1901        2503                    Sausage - Liver         1
1892        2503             Pants Custom Dry Clean         1
1893        2503       Pastry - Cheese Baked Scones         1
1894        2503                 Peas - Pigeon, Dry         1
1895        2503               Pepsi - Diet, 355 Ml         1
1896        2503        Pork - Bacon, Double Smoked         1
1897        2503                Raspberries - Fresh         1
1898        2503                   Salsify, Organic         1
1899        2503                Sauce - Hollandaise         1
1900        2503                Sausage - Breakfast         1
1902        2503         Soup - Campbells, Cream Of         1
1890        2503             Nut - Chestnuts, Whole         1
1903        2503       Soup - Canadian Pea, Dry Mix         1
1904        2503                 Tea - Decaf Lipton         1
1905        2503                          Tia Maria         1
1906        2503                  Veal - Sweetbread         1
1907        2503         Wine - Crozes Hermitage E.         1
1908        2503         Wine - Magnotta - Cab Sauv         1
1909        2503                Wine - Red, Cooking         1
1910        2503   Wine - White, Schroder And Schyl         1
1891        2503   Oil - Shortening - All - Purpose         1
1865        2503          Appetizer - Mushroom Tart         1
1889        2503               Lamb - Pieces, Diced         1
1866        2503          Appetizer - Sausage Rolls         1
1867        2503              Bandage - Fexible 1x3         1
1869        2503     Beef - Montreal Smoked Brisket         1
1870        2503           Beef - Top Sirloin - Aaa         1
1871        2503                 Beef Ground Medium         1
1872        2503        Beets - Candy Cane, Organic         1
1873        2503             Bread - English Muffin         1
1874        2503               Bread Crumbs - Panko         1
1876        2503         Cake - Cake Sheet Macaroon         1
1877        2503   Cheese - Boursin, Garlic / Herbs         1
1878        2503           Cheese - Taleggio D.o.p.         1
1879        2503                      Chef Hat 20cm         1
1880        2503             Coffee Decaf Colombian         1
1881        2503                    Cream Of Tartar         1
1882        2503                    Extract - Lemon         1
1883        2503                     Fond - Neutral         1
1884        2503                      Hersey Shakes         1
1885        2503      Ice Cream Bar - Hageen Daz To         1
1886        2503                       Juice - Lime         1
1887        2503                   Ketchup - Tomato         1
1911        2503                      Yoghurt Tubes         1

In [271]:
df_rank.head()

CustomerID                        ProductName  Quantity
1888        2503              Knife Plastic - White         2
1868        2503  Bar - Granola Trail Mix Fruit Nut         2
1875        2503                  Butter - Unsalted         2
1901        2503                    Sausage - Liver         1
1892        2503             Pants Custom Dry Clean         1

## Step 7: Filter the list for products that the chosen customer has not yet purchased and then recommend the top 5 products with the highest quantities that are left.

- Merge the ranked products data frame with the customer product matrix on the ProductName field.
- Filter for records where the chosen customer has not purchased the product.
- Show the top 5 results.

In [303]:
df_p = data.groupby(["CustomerID","ProductName"])['Quantity'].sum().reset_index()

df_2 = df_rank.merge(df_p, how="right", on='ProductName').fillna(0)
df_3 = df_2[df_2["CustomerID_y"]==33].sort_values("Quantity_x", ascending=True)
df_4 = df_3[df_3["CustomerID_x"]==0.0].sort_values("Quantity_y", ascending=False)
list(df_4["ProductName"].head())

['Lettuce - Spring Mix',
 'Grouper - Fresh',
 'Veal - Inside, Choice',
 'Bread - Italian Roll With Herbs',
 'Assorted Desserts']

## Step 8: Now that we have generated product recommendations for a single user, put the pieces together and iterate over a list of all CustomerIDs.

- Create an empty dictionary that will hold the recommendations for all customers.
- Create a list of unique CustomerIDs to iterate over.
- Iterate over the customer list performing steps 4 through 7 for each and appending the results of each iteration to the dictionary you created.

In [482]:
customer_list = []
#customer_dict = {}
df_p = data.groupby(["CustomerID","ProductName"])['Quantity'].sum().reset_index()

for x in df_p["CustomerID"].unique():
    df_2 = df_rank.merge(df_p, how="right", on='ProductName').fillna(0)
    df_3 = df_2[df_2["CustomerID_y"]== x].sort_values("Quantity_x", ascending=True)
    df_4 = df_3[df_3["CustomerID_x"]==0.0].sort_values("Quantity_y", ascending=False).head()
    df_5 = pd.DataFrame(df_4, columns=["CustomerID_y", "ProductName"]).head()
    #df_6 = df_5.drop_duplicates()
    customer_dict = {}
    customer_dict['CustomerID_y'] = x
    customer_dict['ProductName'] = list(df_5["ProductName"])
    customer_list.append(customer_dict)
    print(customer_list)

[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}]
[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}]
[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}]
[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', '

[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}, {'CustomerID_y': 356, 'ProductName': ['Scallops - 10/20', 'Cinnamon Buns Sticky', 'Sobe - Tropical Energy', 'Spoon - Soup, Plastic', 'Mayonnaise - Individual Pkg']}, {'CustomerID_y': 412, 'ProductName': ['Ecolab - Lime - A - Way 4/4 L', 'Pernod', 'Sauce - Demi Glace', 'Spinach - Baby', 'Flavouring - Orange']}, {'CustomerID_y': 464, 'ProductName': ['Kellogs All Bran Bars', 'Vaccum Bag 10x13', 'Phyllo Dough', 'Gloves - Goldtouch Disposable', 'Cheese Cloth No 100']}, {'CustomerID_y': 477, 'ProductName': ['Bacardi Breezer - Tropical', 'Wine - C

[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}, {'CustomerID_y': 356, 'ProductName': ['Scallops - 10/20', 'Cinnamon Buns Sticky', 'Sobe - Tropical Energy', 'Spoon - Soup, Plastic', 'Mayonnaise - Individual Pkg']}, {'CustomerID_y': 412, 'ProductName': ['Ecolab - Lime - A - Way 4/4 L', 'Pernod', 'Sauce - Demi Glace', 'Spinach - Baby', 'Flavouring - Orange']}, {'CustomerID_y': 464, 'ProductName': ['Kellogs All Bran Bars', 'Vaccum Bag 10x13', 'Phyllo Dough', 'Gloves - Goldtouch Disposable', 'Cheese Cloth No 100']}, {'CustomerID_y': 477, 'ProductName': ['Bacardi Breezer - Tropical', 'Wine - C

[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}, {'CustomerID_y': 356, 'ProductName': ['Scallops - 10/20', 'Cinnamon Buns Sticky', 'Sobe - Tropical Energy', 'Spoon - Soup, Plastic', 'Mayonnaise - Individual Pkg']}, {'CustomerID_y': 412, 'ProductName': ['Ecolab - Lime - A - Way 4/4 L', 'Pernod', 'Sauce - Demi Glace', 'Spinach - Baby', 'Flavouring - Orange']}, {'CustomerID_y': 464, 'ProductName': ['Kellogs All Bran Bars', 'Vaccum Bag 10x13', 'Phyllo Dough', 'Gloves - Goldtouch Disposable', 'Cheese Cloth No 100']}, {'CustomerID_y': 477, 'ProductName': ['Bacardi Breezer - Tropical', 'Wine - C

[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}, {'CustomerID_y': 356, 'ProductName': ['Scallops - 10/20', 'Cinnamon Buns Sticky', 'Sobe - Tropical Energy', 'Spoon - Soup, Plastic', 'Mayonnaise - Individual Pkg']}, {'CustomerID_y': 412, 'ProductName': ['Ecolab - Lime - A - Way 4/4 L', 'Pernod', 'Sauce - Demi Glace', 'Spinach - Baby', 'Flavouring - Orange']}, {'CustomerID_y': 464, 'ProductName': ['Kellogs All Bran Bars', 'Vaccum Bag 10x13', 'Phyllo Dough', 'Gloves - Goldtouch Disposable', 'Cheese Cloth No 100']}, {'CustomerID_y': 477, 'ProductName': ['Bacardi Breezer - Tropical', 'Wine - C

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}, {'CustomerID_y': 356, 'ProductName': ['Scallops - 10/20', 'Cinnamon Buns Sticky', 'Sobe - Tropical Energy', 'Spoon - Soup, Plastic', 'Mayonnaise - Individual Pkg']}, {'CustomerID_y': 412, 'ProductName': ['Ecolab - Lime - A - Way 4/4 L', 'Pernod', 'Sauce - Demi Glace', 'Spinach - Baby', 'Flavouring - Orange']}, {'CustomerID_y': 464, 'ProductName': ['Kellogs All Bran Bars', 'Vaccum Bag 10x13', 'Phyllo Dough', 'Gloves - Goldtouch Disposable', 'Cheese Cloth No 100']}, {'CustomerID_y': 477, 'ProductName': ['Bacardi Breezer - Tropical', 'Wine - C

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[{'CustomerID_y': 33, 'ProductName': ['Lettuce - Spring Mix', 'Grouper - Fresh', 'Veal - Inside, Choice', 'Bread - Italian Roll With Herbs', 'Assorted Desserts']}, {'CustomerID_y': 200, 'ProductName': ['Lamb - Ground', 'Olives - Kalamata', 'Tahini Paste', 'Remy Red', 'Bacardi Breezer - Tropical']}, {'CustomerID_y': 264, 'ProductName': ['Chocolate - Dark', 'Mushrooms - Black, Dried', 'Guinea Fowl', 'Apricots - Halves', 'Lemonade - Natural, 591 Ml']}, {'CustomerID_y': 356, 'ProductName': ['Scallops - 10/20', 'Cinnamon Buns Sticky', 'Sobe - Tropical Energy', 'Spoon - Soup, Plastic', 'Mayonnaise - Individual Pkg']}, {'CustomerID_y': 412, 'ProductName': ['Ecolab - Lime - A - Way 4/4 L', 'Pernod', 'Sauce - Demi Glace', 'Spinach - Baby', 'Flavouring - Orange']}, {'CustomerID_y': 464, 'ProductName': ['Kellogs All Bran Bars', 'Vaccum Bag 10x13', 'Phyllo Dough', 'Gloves - Goldtouch Disposable', 'Cheese Cloth No 100']}, {'CustomerID_y': 477, 'ProductName': ['Bacardi Breezer - Tropical', 'Wine - C

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
# Algo estoy haciendo mal y no doy con la tecla, porque sí me aparece un diccionario con
# su customer id correspondiente y su lista... pero se me duplican

##  Step 9: Store the results in a Pandas data frame. The data frame should a column for Customer ID and then a column for each of the 5 product recommendations for each customer.

In [543]:
p_customer_list = pd.DataFrame(customer_list)
p_customer_list

CustomerID_y                                        ProductName
0              33  [Lettuce - Spring Mix, Grouper - Fresh, Veal -...
1             200  [Lamb - Ground, Olives - Kalamata, Tahini Past...
2             264  [Chocolate - Dark, Mushrooms - Black, Dried, G...
3             356  [Scallops - 10/20, Cinnamon Buns Sticky, Sobe ...
4             412  [Ecolab - Lime - A - Way 4/4 L, Pernod, Sauce ...
..            ...                                                ...
995         97928  [Apricots - Halves, Tea - Jasmin Green, Cookie...
996         98069  [Chocolate - Semi Sweet, Calets, Hot Chocolate...
997         98159  [Squid - Tubes / Tenticles 10/20, Papayas, Cam...
998         98185  [Bagel - Plain, Scallops - Live In Shell, Muss...
999         98200  [Vol Au Vents, Ocean Spray - Kiwi Strawberry, ...

[1000 rows x 2 columns]

In [526]:
#p_customer_list[["Prod1", "Prod2", "Prod3", "Prod4", "Prod5"]]= p_customer_list["ProductName"].str.split(pat=",", expand=True)
#df.DataFrame(df['Col'].to_list(), columns = ['c1', 'c2', 'c3'])

In [544]:
p_customer_list_1 = pd.DataFrame(p_customer_list['ProductName'].to_list(), columns = ['Prod1', 'Prod2', 'Prod3', 'Prod4', 'Prod5'])
p_customer_list_1

Prod1                          Prod2  \
0               Lettuce - Spring Mix                Grouper - Fresh   
1                      Lamb - Ground              Olives - Kalamata   
2                   Chocolate - Dark       Mushrooms - Black, Dried   
3                   Scallops - 10/20           Cinnamon Buns Sticky   
4      Ecolab - Lime - A - Way 4/4 L                         Pernod   
..                               ...                            ...   
995                Apricots - Halves             Tea - Jasmin Green   
996   Chocolate - Semi Sweet, Calets     Hot Chocolate - Individual   
997  Squid - Tubes / Tenticles 10/20                        Papayas   
998                    Bagel - Plain       Scallops - Live In Shell   
999                     Vol Au Vents  Ocean Spray - Kiwi Strawberry   

                      Prod3                            Prod4  \
0     Veal - Inside, Choice  Bread - Italian Roll With Herbs   
1              Tahini Paste                         Remy Red   
2               Guinea Fowl                Apricots - Halves   
3    Sobe - Tropical Energy            Spoon - Soup, Plastic   
4        Sauce - Demi Glace                   Spinach - Baby   
..                      ...                              ...   
995   Cookie Dough - Double      Bouq All Italian - Primerba   
996        Mustard Prepared     Chocolate - Compound Coating   
997                 Campari              Tray - 16in Rnd Blk   
998    Mussels - Cultivated     Whmis - Spray Bottle Trigger   
999              Dried Figs         Soup - Campbells, Lentil   

                           Prod5  
0              Assorted Desserts  
1     Bacardi Breezer - Tropical  
2     Lemonade - Natural, 591 Ml  
3    Mayonnaise - Individual Pkg  
4            Flavouring - Orange  
..                           ...  
995           Halibut - Fletches  
996            Assorted Desserts  
997      Cheese - Parmesan Cubes  
998         Bread - Bistro White  
999             Sea Bass - Whole  

[1000 rows x 5 columns]

In [546]:
df_9 = pd.concat([p_customer_list["CustomerID_y"], p_customer_list_1], axis=1)
df_9

CustomerID_y                            Prod1  \
0              33             Lettuce - Spring Mix   
1             200                    Lamb - Ground   
2             264                 Chocolate - Dark   
3             356                 Scallops - 10/20   
4             412    Ecolab - Lime - A - Way 4/4 L   
..            ...                              ...   
995         97928                Apricots - Halves   
996         98069   Chocolate - Semi Sweet, Calets   
997         98159  Squid - Tubes / Tenticles 10/20   
998         98185                    Bagel - Plain   
999         98200                     Vol Au Vents   

                             Prod2                   Prod3  \
0                  Grouper - Fresh   Veal - Inside, Choice   
1                Olives - Kalamata            Tahini Paste   
2         Mushrooms - Black, Dried             Guinea Fowl   
3             Cinnamon Buns Sticky  Sobe - Tropical Energy   
4                           Pernod      Sauce - Demi Glace   
..                             ...                     ...   
995             Tea - Jasmin Green   Cookie Dough - Double   
996     Hot Chocolate - Individual        Mustard Prepared   
997                        Papayas                 Campari   
998       Scallops - Live In Shell    Mussels - Cultivated   
999  Ocean Spray - Kiwi Strawberry              Dried Figs   

                               Prod4                        Prod5  
0    Bread - Italian Roll With Herbs            Assorted Desserts  
1                           Remy Red   Bacardi Breezer - Tropical  
2                  Apricots - Halves   Lemonade - Natural, 591 Ml  
3              Spoon - Soup, Plastic  Mayonnaise - Individual Pkg  
4                     Spinach - Baby          Flavouring - Orange  
..                               ...                          ...  
995      Bouq All Italian - Primerba           Halibut - Fletches  
996     Chocolate - Compound Coating            Assorted Desserts  
997              Tray - 16in Rnd Blk      Cheese - Parmesan Cubes  
998     Whmis - Spray Bottle Trigger         Bread - Bistro White  
999         Soup - Campbells, Lentil             Sea Bass - Whole  

[1000 rows x 6 columns]

## Step 10: Change the distance metric used in Step 3 to something other than euclidean (correlation, cityblock, consine, jaccard, etc.). Regenerate the recommendations for all customers and note the differences.

In [553]:
cosine_dist_norm = pd.DataFrame(1/(1 + squareform(pdist(pivot_data_T, 'cosine'))),
                                index=pivot_data_T.index,
                                columns=pivot_data_T.index)
cosine_dist_norm


CustomerID     33        200       264       356       412       464    \
CustomerID                                                               
33          1.000000  0.532692  0.565443  0.550466  0.538239  0.540192   
200         0.532692  1.000000  0.540444  0.536424  0.514712  0.523506   
264         0.565443  0.540444  1.000000  0.534784  0.555621  0.529915   
356         0.550466  0.536424  0.534784  1.000000  0.533110  0.525642   
412         0.538239  0.514712  0.555621  0.533110  1.000000  0.532824   
...              ...       ...       ...       ...       ...       ...   
97928       0.516959  0.527408  0.563065  0.534488  0.541355  0.543480   
98069       0.529475  0.569724  0.551325  0.516147  0.523256  0.524409   
98159       0.521380  0.540096  0.543480  0.543866  0.536914  0.538794   
98185       0.523291  0.528386  0.551922  0.547973  0.553549  0.534833   
98200       0.533971  0.526533  0.533084  0.537860  0.562502  0.556081   

CustomerID     477       639       649       669    ...     97697     97753  \
CustomerID                                          ...                       
33          0.524859  0.527028  0.530712  0.536037  ...  0.529019  0.521742   
200         0.546896  0.520122  0.540444  0.545661  ...  0.550794  0.536424   
264         0.532824  0.517251  0.529915  0.525866  ...  0.550500  0.530173   
356         0.533110  0.545887  0.521187  0.526088  ...  0.537266  0.525862   
412         0.544000  0.547992  0.528487  0.542463  ...  0.526924  0.551365   
...              ...       ...       ...       ...  ...       ...       ...   
97928       0.541355  0.540216  0.538794  0.530182  ...  0.536626  0.548680   
98069       0.531497  0.529743  0.537530  0.538198  ...  0.531254  0.533372   
98159       0.536914  0.530730  0.548247  0.534794  ...  0.536626  0.553579   
98185       0.533156  0.549319  0.539005  0.519093  ...  0.525220  0.511188   
98200       0.535715  0.534283  0.524409  0.552262  ...  0.531254  0.528959   

CustomerID     97769     97793     97900     97928     98069     98159  \
CustomerID                                                               
33          0.534813  0.513650  0.534245  0.516959  0.529475  0.521380   
200         0.557488  0.543589  0.539102  0.527408  0.569724  0.540096   
264         0.533903  0.537132  0.551752  0.563065  0.551325  0.543480   
356         0.538805  0.532472  0.533641  0.534488  0.516147  0.543866   
412         0.532274  0.535338  0.540327  0.541355  0.523256  0.536914   
...              ...       ...       ...       ...       ...       ...   
97928       0.529168  0.546881  0.560888  1.000000  0.560377  0.552632   
98069       0.532529  0.521683  0.558825  0.560377  1.000000  0.555585   
98159       0.542736  0.527112  0.542029  0.552632  0.555585  1.000000   
98185       0.542504  0.537511  0.533689  0.530465  0.541462  0.551465   
98200       0.545846  0.526247  0.545083  0.515881  0.544715  0.532803   

CustomerID     98185     98200  
CustomerID                      
33          0.523291  0.533971  
200         0.528386  0.526533  
264         0.551922  0.533084  
356         0.547973  0.537860  
412         0.553549  0.562502  
...              ...       ...  
97928       0.530465  0.515881  
98069       0.541462  0.544715  
98159       0.551465  0.532803  
98185       1.000000  0.553991  
98200       0.553991  1.000000  

[1000 rows x 1000 columns]